In [1]:
import math
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import matplotlib.colors as colors

import folium
from folium import Choropleth, Marker, Circle
from folium.plugins import HeatMap,MarkerCluster

# Displaying interactive maps

In [2]:
def embed_map(m, file_name):
    from IPython.display import IFrame
    m.save(file_name)
    return IFrame(file_name, width='100%', height='500px')

In [3]:
plate_boundaries = gpd.read_file("archive/Plate_Boundaries/Plate_Boundaries/Plate_Boundaries.shp")
# shapefile/GeoPandas 默认坐标顺序是 (lon, lat) → 即 (经度, 纬度)
# 但 folium 要的是 [lat, lon] → 即 [纬度, 经度]

# 反转合并
plate_boundaries['coordinates'] = plate_boundaries.apply(lambda x: [(b,a) for (a,b) in list(x.geometry.coords)], axis='columns')
plate_boundaries.drop('geometry', axis=1, inplace=True)

plate_boundaries.head()

HAZ_PLATES                                         HAZ_PLAT_1  HAZ_PLAT_2  \
0     TRENCH                              SERAM TROUGH (ACTIVE)        6722   
1     TRENCH                                       WETAR THRUST        6722   
2     TRENCH  TRENCH WEST OF LUZON (MANILA TRENCH) NORTHERN ...        6621   
3     TRENCH                                       BONIN TRENCH        9821   
4     TRENCH                                  NEW GUINEA TRENCH        8001   

   Shape_Leng                                        coordinates  
0    5.843467  [(-5.444200361999947, 133.6808931800001), (-5....  
1    1.829013  [(-7.760600482999962, 125.47879802900002), (-7...  
2    6.743604  [(19.817899819000047, 120.09999798800004), (19...  
3    8.329381  [(26.175899215000072, 143.20620700100005), (26...  
4   11.998145  [(0.41880004000006466, 132.8273013480001), (0....

In [4]:
earthquakes = pd.read_csv("archive/earthquakes1970-2014.csv", parse_dates=["DateTime"])
earthquakes.head()

DateTime  Latitude  Longitude  Depth  Magnitude MagType  \
0 1970-01-04 17:00:40.200    24.139    102.503   31.0        7.5      Ms   
1 1970-01-06 05:35:51.800    -9.628    151.458    8.0        6.2      Ms   
2 1970-01-08 17:12:39.100   -34.741    178.568  179.0        6.1      Mb   
3 1970-01-10 12:07:08.600     6.825    126.737   73.0        6.1      Mb   
4 1970-01-16 08:05:39.000    60.280   -152.660   85.0        6.0      ML   

   NbStations  Gap  Distance  RMS Source       EventID  
0        90.0  NaN       NaN  0.0    NEI  1.970010e+09  
1        85.0  NaN       NaN  0.0    NEI  1.970011e+09  
2        59.0  NaN       NaN  0.0    NEI  1.970011e+09  
3        91.0  NaN       NaN  0.0    NEI  1.970011e+09  
4         0.0  NaN       NaN  NaN     AK           NaN

In [5]:
m_1 = folium.Map(location=[35,136], tiles='cartodbpositron', zoom_start=5)
for i in range(len(plate_boundaries)):
    folium.PolyLine(locations=plate_boundaries.coordinates.iloc[i], weight=2, color='black').add_to(m_1)
HeatMap(data=earthquakes[['Latitude','Longitude']],radius=20).add_to(m_1)

In [6]:
# Show the map
# embed_map(m_1, 'q_1.html')
# 使用浏览器打开文件即可显示交互式地图

# Plotting Points

In [7]:
crimes = pd.read_csv('archive/crimes-in-boston/crimes-in-boston/crime.csv', encoding='latin1')
crimes.head()

INCIDENT_NUMBER  OFFENSE_CODE    OFFENSE_CODE_GROUP   OFFENSE_DESCRIPTION  \
0      I182070945           619               Larceny    LARCENY ALL OTHERS   
1      I182070943          1402             Vandalism             VANDALISM   
2      I182070941          3410                 Towed   TOWED MOTOR VEHICLE   
3      I182070940          3114  Investigate Property  INVESTIGATE PROPERTY   
4      I182070938          3114  Investigate Property  INVESTIGATE PROPERTY   

  DISTRICT REPORTING_AREA SHOOTING     OCCURRED_ON_DATE  YEAR  MONTH  \
0      D14            808      NaN  2018-09-02 13:00:00  2018      9   
1      C11            347      NaN  2018-08-21 00:00:00  2018      8   
2       D4            151      NaN  2018-09-03 19:27:00  2018      9   
3       D4            272      NaN  2018-09-03 21:16:00  2018      9   
4       B3            421      NaN  2018-09-03 21:05:00  2018      9   

  DAY_OF_WEEK  HOUR    UCR_PART       STREET        Lat       Long  \
0      Sunday    13    Part One   LINCOLN ST  42.357791 -71.139371   
1     Tuesday     0    Part Two     HECLA ST  42.306821 -71.060300   
2      Monday    19  Part Three  CAZENOVE ST  42.346589 -71.072429   
3      Monday    21  Part Three   NEWCOMB ST  42.334182 -71.078664   
4      Monday    21  Part Three     DELHI ST  42.275365 -71.090361   

                      Location  
0  (42.35779134, -71.13937053)  
1  (42.30682138, -71.06030035)  
2  (42.34658879, -71.07242943)  
3  (42.33418175, -71.07866441)  
4  (42.27536542, -71.09036101)

In [8]:
daytime_robberies = crimes[((crimes.OFFENSE_CODE_GROUP == 'Robbery') & (crimes.HOUR.isin(range(9,18))))]

## Marker

```python
for idx, row in daytime_robberies.iterrows():
```
一行一行地取数据，每次循环 idx 是当前行号，row 是那一行的内容

```bash
folium.Marker() 函数

参数名 | 类型 | 作用说明
|------|------|------|
location | list [lat, lon] | 必填，标记的位置（纬度, 经度）
popup | str 或 HTML/folium 对象 | 点击标记时弹出的信息框内容
tooltip | str 或 HTML/folium 对象 | 鼠标悬停时显示的提示
icon | folium.Icon() 或 folium.DivIcon() | 图标样式（颜色、图案、字体）
draggable | bool | 是否可以拖动标记点，默认 False

In [9]:
# Create a map
m_2 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=13)

# Add points to the map
for idx, row in daytime_robberies.iterrows():
    if not math.isnan(row['Lat']) and not math.isnan(row['Long']):
        Marker([row['Lat'], row['Long']]).add_to(m_2)

# Display the map
m_2

## Icon

```python
folium.Icon(
    color='blue',        # 图标颜色：blue, green, red, purple, orange, darkred...
    icon='info-sign',    # 图标图案（Leaflet 支持的图标名）
    prefix='glyphicon'   # 图标集（前缀），默认使用 bootstrap glyphicon，可换成 'fa'（Font Awesome）
)

In [10]:
m_3 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=13)

for idx,row in daytime_robberies.iterrows():
    if not math.isnan(row['Lat']) and not math.isnan(row['Long']):
        Marker(
            location=[row['Lat'],row['Long']],
            tooltip=row['HOUR'],
            icon=folium.Icon(color='cadetblue', icon_color='white',icon='camera',prefix='fa')
        ).add_to(m_3)

m_3

🔹 Font Awesome 图标：
https://fontawesome.com/v4.7/icons/

🔹 Bootstrap Glyphicon 图标：
https://www.w3schools.com/icons/bootstrap_icons_glyphicons.asp

## MarkerCluster

In [11]:
m4 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=13)

mc = MarkerCluster()
for idx,row in daytime_robberies.iterrows():
    if not math.isnan(row['Lat']) and not math.isnan(row['Long']):
        mc.add_child(Marker([row['Lat'],row['Long']]))
m4.add_child(mc)
m4

# Bubble maps

```python
folium.Circle(
    location,
    radius=1000,
    popup=None,
    tooltip=None,
    color='#3388ff',
    weight=3,
    fill=True,
    fill_color=None,
    fill_opacity=0.2,
    **kwargs
)

|参数 | 类型 | 含义|
|------|------|------|
|location | [lat, lon] 列表 | 圆心位置（纬度，经度）|
|radius | 数值（米） | 圆的半径，单位是米|
|popup | 字符串或 HTML | 点击圆时弹出的对话框内容|
|tooltip | 字符串 | 鼠标悬浮时显示的提示信息|
|color | 颜色名或十六进制色 | 圆的边框颜色，例如 'red', '#ff0000'|
|weight | 数值 | 圆边框的线宽（默认是 3）|
|fill | 布尔值 | 是否填充圆内部颜色，默认是 False|
|fill_color | 颜色名或十六进制色 | 圆内部的填充颜色（默认与 color 一样）|
|fill_opacity | 0 到 1 的浮点数 | 圆内部颜色的透明度|
|opacity | 0 到 1 的浮点数 | 圆边框的透明度|

In [12]:
m_5 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=13)

# 用 matplotlib.cm 自己映射颜色值
norm = colors.Normalize(vmin=0, vmax=23)
cmap = plt.get_cmap('viridis')  # 你可以换成 'plasma', 'coolwarm' 等
def color_producer(hour):
    rgba = cmap(norm(hour))
    # rgba 是 (R, G, B, A)，我们取前 3 位，转成 hex
    return colors.to_hex(rgba)


# Add a bubble map to the base map
for idx,row in daytime_robberies.iterrows():
    if not math.isnan(row['Lat']) and not math.isnan(row['Long']):
        Circle(
            location=[row['Lat'], row['Long']],
            radius=20,
            tooltip=f"{row['HOUR']} o'clock",
            fill=True,
            color=color_producer(row['HOUR'])).add_to(m_5)

# Display the map
m_5

# Heat maps

In [13]:
# Create a base map
m_6 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=12)

# Add a heatmap to the base map
crimes.dropna(axis=0,inplace=True)
HeatMap(data=crimes[['Lat', 'Long']], radius=10).add_to(m_6)

# Display the map
m_6

# PolyLine

```bash
folium.PolyLine 用于在地图上绘制折线 / 路径 / 边界线段。你可以把它想象成用一支笔在地图上“连点成线”。
```
它非常适合以下场景：

- 显示公交线路 / 出行路径

- 描述某个区域的边界

- 表示某人/物的轨迹（比如 GPS 路径）

```python
folium.PolyLine(
    locations,         # 一组 [纬度, 经度] 坐标组成的列表
    color='blue',      # 线的颜色
    weight=3,          # 线的粗细（单位像素）
    opacity=0.8        # 透明度
).add_to(map_object)

参数名 | 类型 | 含义说明
|------|------|------|
locations | list of [lat, lon] 坐标 | 组成折线的坐标点
color | str | 线条颜色，比如 'red', 'blue', '#00ff00'
weight | int | 线的粗细（像素），默认 2
opacity | float | 透明度（0 到 1）
popup | str / Popup对象 | 点击线条时弹出信息
tooltip | str / Tooltip对象 | 鼠标悬停时提示文字
dash_array | str | 例如 '5, 5' 会画虚线，None 为实线
line_cap | str | 线段末端样式（如 round, square）

In [14]:
# 创建地图
m_7 = folium.Map(location=[35,136], tiles='cartodbpositron', zoom_start=5) 

# 绘制板块边界
for i in range(len(plate_boundaries)):
    folium.PolyLine(
        locations=plate_boundaries.loc[i,'coordinates'],
        color='black',
        weight=1
    ).add_to(m_7)

# 绘制地震强度热力图
HeatMap(
    data=earthquakes[['Latitude','Longitude']],
    radius=20
).add_to(m_7)

m_7

# Choropleth maps

“分级统计地图” 或 “颜色分级图”

In [15]:
# GeoDataFrame with geographical boundaries of Boston police districts
# 行政边界
districts_full = gpd.read_file('archive/Police_Districts/Police_Districts/Police_Districts.shp')
districts = districts_full[["DISTRICT", "geometry"]].set_index("DISTRICT")
districts.head()

geometry
DISTRICT                                                   
A15       MULTIPOLYGON (((-71.07416 42.39051, -71.07415 ...
A7        MULTIPOLYGON (((-70.99644 42.39557, -70.99644 ...
A1        POLYGON ((-71.052 42.36884, -71.05169 42.3687,...
C6        POLYGON ((-71.04406 42.35403, -71.04412 42.353...
D4        POLYGON ((-71.07416 42.35724, -71.07359 42.357...

In [16]:
# Number of crimes in each police district
plot_dict = crimes.DISTRICT.value_counts()
plot_dict.head()

DISTRICT
B2     333
B3     215
C11    177
E13     63
D4      45
Name: count, dtype: int64

```python
folium.Choropleth(
    geo_data,
    data=None,
    columns=None,
    key_on=None,
    bins=None,
    fill_color='YlOrRd',
    fill_opacity=0.6,
    line_opacity=0.2,
    line_color='black',
    legend_name=None,
    reset=True,
    highlight=False,
    name=None,
    overlay=True,
    control=True,
    show=True,
    nan_fill_color='white',
    nan_fill_opacity=0.1,
    smooth_factor=None,
    topojson=None
)


参数 | 类型 | 说明
|------|------|------|
geo_data | dict 或 .geojson 路径 | 地理边界数据，必须是 GeoJSON/TopoJSON 格式
data | DataFrame | 包含要展示的数值的表格数据
columns | list | 指定 [区域名列, 数值列]，对应 DataFrame 中的列名
key_on | str | GeoJSON 中的区域名字段，例如 'feature.properties.Name'
fill_color | str | 色阶方案（colormap），如 'YlOrRd', 'BuPu', 'PuBuGn'
fill_opacity | float | 区域颜色的不透明度（0~1）
line_opacity | float | 区域边界线条的不透明度
legend_name | str | 图例标题，会显示在地图上
bins | list 或 int | 自定义分级（如 [0, 10, 20, 50, 100]）或等级数量（如 6）
nan_fill_color | str | 数据缺失区域的填充颜色
highlight | bool | 鼠标悬停时高亮边界

In [17]:
# Create a base map
m_6 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=12)

# Add a choropleth map to the base map
Choropleth(geo_data=districts.__geo_interface__,    # 把 GeoDataFrame 转为 GeoJSON 字典对象（内存中用）
           data=plot_dict, 
           key_on="feature.id", 
           fill_color='YlGnBu', 
           legend_name='Major criminal incidents (Jan-Aug 2018)',
           highlight=True
          ).add_to(m_6)

# Display the map
m_6
'''
    folium.Choropleth 本身不支持直接添加 tooltip 来显示数值，这是它的一个局限
    但是可以通过配合 folium.GeoJson 叠加一层，添加 tooltip来实现悬停效果,并且支持显示区域名,数值,甚至加粗高亮
'''

'\n    folium.Choropleth 本身不支持直接添加 tooltip 来显示数值，这是它的一个局限\n    但是可以通过配合 folium.GeoJson 叠加一层，添加 tooltip来实现悬停效果,并且支持显示区域名,数值,甚至加粗高亮\n'

In [18]:
# 打印字典结构
districts.__geo_interface__

{'type': 'FeatureCollection',
 'features': [{'id': 'A15',
   'type': 'Feature',
   'properties': {},
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [(((-71.07415718153364, 42.390507686248306),
       (-71.07415424746895, 42.390503696137124),
       (-71.07403961352766, 42.39054086496418),
       (-71.07393964511492, 42.390379143356114),
       (-71.07377237566668, 42.39009698543054),
       (-71.07361166169, 42.389830761341194),
       (-71.07344403708477, 42.389546953156085),
       (-71.07326831318817, 42.38925652728944),
       (-71.0730937070298, 42.388965557003026),
       (-71.07292832121637, 42.38867983419289),
       (-71.07293103519046, 42.38866118498357),
       (-71.07283365981914, 42.38850029570664),
       (-71.07275606610709, 42.38836993909938),
       (-71.07268736490828, 42.38823796794029),
       (-71.0727338745498, 42.38814813477101),
       (-71.07272171746692, 42.388139034570465),
       (-71.07271618331094, 42.38814620998887),
       (-71.07271201154819

结构解释：

- type：始终是 "FeatureCollection"，表示这是一个包含多个“特征”的集合。

- features：一个列表，每个元素表示一个地理对象（即一个区域或一个多边形）。每个元素都是一个字典，包含：

- type：每个特征的类型（通常是 "Feature"）。

- geometry：包含几何数据（比如 Polygon 或 Point）和坐标。

- properties：存储区域的属性数据（比如 Name、Population 等）。